In [3]:
from utils.utils import normalize_series, reshample_time_serie, categorize_precipitation
from api_somo import fetch_and_process_data
from graphics_utils.go import multi_line
import numpy as np
import pandas as pd

# API y parámetros
api_filtrate_seire = "http://127.0.0.1:8000/database/filter-serie/"
params = {
    "station_name": "tumaco",
    "variable_name": "Precipitación acumulada",
    "processing_level_name": "Control de calidad",
    "start_date": "2010-01-01",
    "end_date": "2010-12-31"
}

try:
    # 1. Extracción de datos
    serie_historica = fetch_and_process_data(api_filtrate_seire, params)
    if serie_historica.empty:
        raise ValueError("La serie histórica está vacía.")

    # 2. Limpieza de datos
    serie_historica.loc[serie_historica['qf'] == 9, 'value'] = np.nan

    # Crear un DataFrame con los registros que contienen valores NaN
    registros_nan = serie_historica[serie_historica['value'].isna()]

    # 3. Interpolación inicial para permitir el cálculo de EMA
    serie_historica['interpolated_value'] = serie_historica['value'].interpolate(method='linear')

    # 4. Aplicar filtro EMA
    ema_span = 36  # Número de días para suavizar (puedes ajustarlo según el caso)
    serie_historica['synthetic_value'] = serie_historica['interpolated_value'].ewm(span=ema_span, adjust=False).mean()

    # 5. Imputar valores faltantes con la serie sintetizada
    serie_historica['value_imputed'] = serie_historica['value'].combine_first(serie_historica['synthetic_value'])

    # 6. Remuestreo de la serie imputada
    serie_historica_resample = reshample_time_serie(serie_historica, 'd', 'sum')

    # 7. Normalización
    serie_historica['normalized_value'] = normalize_series(serie_historica['value_imputed'], method='min-max')
    serie_historica_resample['normalized_value'] = normalize_series(serie_historica_resample['value'], method='min-max')

    # 8. Visualización
    series_fig = multi_line(
        original=serie_historica['value'],
        #sintetica=serie_historica['synthetic_value'],
        imputada=serie_historica['value_imputed']
    )
    series_fig.show()

    # 9. Estadísticas descriptivas
    print("Estadísticas descriptivas para los valores imputados:")
    print(serie_historica['value_imputed'].describe())
    print("Estadísticas para la serie remuestreada:")
    print(serie_historica_resample['value'].describe())

except Exception as e:
    print(f"Error: {e}")


Estadísticas descriptivas para los valores imputados:
count    52417.000000
mean         0.064136
std          0.446064
min          0.000000
25%          0.000000
50%          0.000000
75%          0.000000
max         16.700000
Name: value_imputed, dtype: float64
Estadísticas para la serie remuestreada:
count    365.000000
mean       8.755068
std       22.244289
min        0.000000
25%        0.100000
50%        1.400000
75%        7.500000
max      198.000000
Name: value, dtype: float64
